# Single Base Training on GPU1

# Quick Links <a name = "Top"></a>
<ol>
    <li><p><a href = #setup>Set Up</a></p></li>
    <li><p><a href = #Base>Base Training</a></p></li>
</ol>

# Imports

In [1]:
import os
import shutil

#print('Current Conda Environment: {}'.format(os.environ['CONDA_DEFAULT_ENV']))

In [2]:
#pip install talos

In [3]:
import talos as ta
from talos.model import lr_normalizer, early_stopper, hidden_layers

import tensorflow as tf
  
available_gpus = tf.config.experimental.list_physical_devices('GPU')
built_with_cuda = tf.test.is_built_with_cuda()

if not (not available_gpus) & built_with_cuda:
    print("The installed version of TensorFlow {} includes GPU support.\n".format(tf.__version__))
    print("Num GPUs Available: ", len(available_gpus), "\n")
else:
    print("The installed version of TensorFlow {} does not include GPU support.\n".format(tf.__version__))
    
from tensorflow.python.client import device_lib
print(device_lib.list_local_devices())

from tensorflow.compat.v1.keras import callbacks, backend as K
from tensorflow.keras.models import Sequential, load_model
from tensorflow.keras.layers import Dense, Dropout, Flatten
from tensorflow.keras.preprocessing.image import ImageDataGenerator
from tensorflow.keras.applications import VGG16
from tensorflow.keras.applications.resnet50 import ResNet50
from tensorflow.keras.utils import multi_gpu_model
from tensorflow.keras.initializers import glorot_uniform
from tensorflow.keras.optimizers import Adam, Nadam, RMSprop, SGD, Adagrad
from tensorflow.keras.layers import ReLU, LeakyReLU

from datetime import datetime
import pandas as pd
import numpy as np

import time

from numpy.random import seed
seed(1)
tf.random.set_seed(1)

config = tf.compat.v1.ConfigProto()
config.gpu_options.allow_growth=True
config.gpu_options.per_process_gpu_memory_fraction = 0.99
sess = tf.compat.v1.Session(config = config)

#with tf.compat.v1.Session(config = config) as sess: 
#    sess.run()

K.set_session(sess)

The installed version of TensorFlow 2.3.1 does not include GPU support.

[name: "/device:CPU:0"
device_type: "CPU"
memory_limit: 268435456
locality {
}
incarnation: 1404228243190512059
, name: "/device:XLA_CPU:0"
device_type: "XLA_CPU"
memory_limit: 17179869184
locality {
}
incarnation: 12246148168802386075
physical_device_desc: "device: XLA_CPU device"
, name: "/device:XLA_GPU:0"
device_type: "XLA_GPU"
memory_limit: 17179869184
locality {
}
incarnation: 16479894666138976682
physical_device_desc: "device: XLA_GPU device"
]


# Hilfsfunktionen

### Output Directory

* <i>SSD</i>, falls genug Speicher auf SSD im SymLink <i>fast_output</i> verfügbar ist
* <i>HDD</i>, falls möglicherweise zu wenig SSD-Speicher verfügbar ist $\rightarrow$ <i>output</i>

In [4]:
from enum import IntEnum

class OutputDirectory(IntEnum):
    HDD = 0
    SSD = 1
    
output_path = ['output', 'fast_output']

### Convert Label_Type into suitable label names.
$\Rightarrow$ Angular / Normalized $\rightarrow$ ['Elevation', 'Azimuth']

$\Rightarrow$ Stereographic $\rightarrow$ ['S_x', 'S_y']

In [5]:
def get_Label_Names(label_type):
    if label_type == 'Angular' or label_type == 'Normalized':
        return ['Elevation', 'Azimuth']
    elif label_type == 'Stereographic':
        return ['S_x', 'S_y']
    else:
        assert(True, 'LabelType Invalid')
        return None

### Benutzerdefinierte Kostenfunktion & Metrik

In [6]:
def circular_mse(y_true, y_pred):
    max_error = tf.constant(360, dtype = 'float32')
    return K.mean(K.square(K.minimum(K.abs(y_pred - y_true), max_error - K.abs(y_pred - y_true))), axis = -1)

def circular_mae(y_true, y_pred):
    max_error = tf.constant(360, dtype = 'float32')
    return K.mean(K.minimum(K.abs(y_pred - y_true), K.abs(max_error - K.abs(y_pred - y_true))), axis = -1)

def custom_mae(y_true, y_pred):
    return K.mean(K.abs(y_pred - y_true), axis = -1)

### Convert String into Reduction Metric Function

In [7]:
def get_Reduction_Metric(metric):
    
    if metric == 'custom_mae':
        return [custom_mae]
    elif metric == 'tf.keras.metrics.MeanAbsoluteError()':
        return [tf.keras.metrics.MeanAbsoluteError()]
    elif metric == 'circular_mae':
        return [circular_mae]
    elif metric == 'mean_squared_error':
        return ['mean_squared_error']
    else:
        assert(False, 'Metric yet unknown - Please modify get_Reduction_Metric to meet your requirements')
        return None

### Generierung Bottleneck-Features

In [8]:
def create_bottleneck_features(train_generator, valid_generator, bottleneck):
        
    print('Creating bottleneck features...')
    if(_NET == 'VGG16'):
        model = VGG16(include_top = False, weights = 'imagenet')
    elif(_NET == 'RESNET'):
        model = ResNet50(include_top = False, weights = 'imagenet')
    else:
        print('ERROR NET SPELLED WRONG')
        
    #bottleneck_features_train = model.predict_generator(train_generator, train_generator.n // train_generator.batch_size)
    bottleneck_features_train = model.predict(train_generator)
    np.save(open(_LOG_DIR + 'Train_' + bottleneck, 'wb'), bottleneck_features_train)
        
    #bottleneck_features_valid = model.predict_generator(valid_generator, valid_generator.n // valid_generator.batch_size)
    bottleneck_features_valid = model.predict(valid_generator)
    np.save(open(_LOG_DIR + 'Valid_'  + bottleneck, 'wb'), bottleneck_features_valid)

### Generierung Datenpipeline (Angepasst für Talos)

In [9]:
def prepare_data(batch_size, num_samples, label_type):
    #print(_CSV_FILE)
    df = pd.read_csv(_CSV_FILE)
    df_shuffled = df.sample(frac = 1, random_state = 1)
    df_train = df_shuffled[0 : int(num_samples * 0.8 // batch_size * batch_size)]   
    df_valid = df_shuffled.drop(df_shuffled.index[0: df_train.shape[0]])[0 : int(num_samples * 0.2 // batch_size * batch_size)]
    
    train_labels = df_train.drop(['Filename'], axis = 1).values
    valid_labels = df_valid.drop(['Filename'], axis = 1).values
    
    bottleneck = 'Bottleneck_Features_{}_{}.npy'.format(str(num_samples), str(batch_size))                                       
    if not os.path.exists(_LOG_DIR + 'Train_' + bottleneck):
        
        if _USE_DATA_AUGMENTATION:
            train_data_generator = ImageDataGenerator(
                rescale = 1./255, 
                width_shift_range = 0.1,
                height_shift_range = 0.1, 
                zoom_range = 0.1,
                brightness_range = (0.25, 0.75),
                fill_mode = 'nearest'
            )
        else:
            train_data_generator = ImageDataGenerator(
                rescale = 1./255
            )
            
        valid_data_generator = ImageDataGenerator(
            rescale = 1./255
        )
    
        #print('Y-Col: {}'.format(get_Label_Names(label_type)))
        
        train_generator = train_data_generator.flow_from_dataframe(
            dataframe = df_train,
            directory = _IMAGE_DIR,
            x_col = 'Filename',
            y_col = get_Label_Names(label_type),
            class_mode = 'raw',
            target_size = (224, 224),
            color_mode = 'rgb',
            shuffle = False,
            seed = 1,
            batch_size = batch_size
        )
    
        valid_generator = valid_data_generator.flow_from_dataframe(
            dataframe = df_valid,
            directory = _IMAGE_DIR,
            x_col = 'Filename',
            y_col = get_Label_Names(label_type),
            class_mode = 'raw',
            target_size = (224, 224),
            color_mode = 'rgb',
            shuffle = False,
            seed = 1,
            batch_size = batch_size
        )
                                                        
        create_bottleneck_features(train_generator, valid_generator, bottleneck)
        
    train_features = np.load(open(_LOG_DIR + 'Train_' + bottleneck, 'rb'))
    valid_features = np.load(open(_LOG_DIR + 'Valid_' + bottleneck, 'rb'))
                                                        
    return train_labels, valid_labels, train_features, valid_features

### Generierung Modell (Angepasst für Talos)

In [10]:
def grid_model_base(x, y, x_val, y_val, params):
    
    global _COUNTER    
    K.clear_session()

    train_labels, valid_labels, train_features, valid_features = prepare_data(params['batch_size'], params['samples'], params['label_type'])

    model = Sequential()
    model.add(Flatten(input_shape = train_features.shape[1 :])) # (7, 7, 512)
    
    dropout_rate = params['dropout']
    first_neuron = params['first_neuron']
    
    if params['activation'] == 'leakyrelu':
        activation_layer = LeakyReLU(alpha = 0.1)
    elif params['activation'] == 'relu':
        activation_layer = ReLU()  
    
    model.add(Dense(units = first_neuron, kernel_initializer = glorot_uniform(seed = 1)))
    model.add(activation_layer)
    if dropout_rate > 0.0:
        model.add(Dropout(rate = dropout_rate))
        
    hidden_neuron_fraction = first_neuron
    for i in range(params['hidden_layers']):
        hidden_neuron_fraction = hidden_neuron_fraction // 2
        model.add(Dense(units = hidden_neuron_fraction, kernel_initializer = glorot_uniform(seed = 1)))
        model.add(activation_layer)
        if dropout_rate > 0.0:
            model.add(Dropout(rate = dropout_rate))
    
    model.add(Dense(units = 2, kernel_initializer = glorot_uniform(seed = 1)))

    #print('Using Loss: {} \nand Reduction Metric: {}'.format(
    #    params['loss_function'], 
    #    get_Reduction_Metric(params['reduction_metric'])))
    
    model.compile(
        optimizer = params['optimizer'](lr = lr_normalizer(params['lr'], params['optimizer'])), 
        loss = params['loss_function'], 
        metrics = get_Reduction_Metric(params['reduction_metric'])
    )
    
    #print('Monitor: {}'.format(params['monitor_value']))
    
    checkpointer = callbacks.ModelCheckpoint(
        filepath = _LOG_DIR + 'Best_Weights_FC_{}.hdf5'.format(_COUNTER),
        monitor = params['monitor_value'],
        verbose = 1,
        save_best_only = True,
        mode = 'min'
    )
    
    startTime = datetime.now()
    out = model.fit(
        x = train_features,
        y = train_labels,
        epochs = params['epochs'],
        validation_data = (valid_features, valid_labels),
        steps_per_epoch = int(params['samples'] * 0.8 // params['batch_size']),
        validation_steps = int(params['samples'] * 0.2 // params['batch_size']),
        #callbacks = [checkpointer]
    )
    print("Time taken:", datetime.now() - startTime)
    
    _COUNTER = _COUNTER + 1
     
    return out, model

# Parameter <a name = "setup"></a><a href = #Top>Up</a></p>

### GridSerach

#### Hyper Parameter

In [11]:
#     Adam = RMSprop + Momentum (lr=0.001)
#     Nadam = Adam RMSprop + Nesterov-Momentum (lr=0.002)
#     RMSprop = (lr=0.001)
#     SGD = (lr=0.01)
#     Adagrad

hyper_parameter = {
    'samples': [20000],
    'epochs': [1],
    'batch_size': [32, 64],
    'optimizer': [Adam],
    'lr': [1, 2, 5],
    'first_neuron': [1024, 2048, 4096],
    'dropout': [0.25, 0.50],
    'activation': ['leakyrelu', 'relu'],
    'hidden_layers': [0, 1, 2, 3, 4],
    # beginning from here, Values should only contain a single entry:
    # ===============================================================
    'label_type': ['Angular'], # Stereographic, Angular, Normalized
    'loss_function': ['mean_squared_error'], # circular_mse
    'reduction_metric': ['custom_mae'], # tf.keras.metrics.MeanAbsoluteError(), circular_mae, custom_mae, mean_squared_error
    'monitor_value': ['val_custom_mae'] # val_custom_mae, val_mean_absolute_error, val_circular_mae, val_loss
}

In [12]:
def get_params():  
    return p

### Dateisystem

In [13]:
_RUN = 'SYNTH'
_LOSS = 'MSE'
_DATASET_NAME = '201129_2031'
_DEVICE = 'GeForce_RTX_2080_Ti' #"/device:GPU:1" #'TITAN_GPU1'

storage = OutputDirectory.SSD # 'fast_output' if ssd storage may suffice, 'output' otherwise

#APPENDIX = 'Stereographic'

#FUNCTION_OVERRIDE = ['mean_squared_error', [custom_mae], 'val_custom_mae'] # None, or e. g. ['mean_squared_error', [circular_mae], 'val_circular_mae']

if hyper_parameter['label_type'][0] == 'Stereographic':
    _CSV_FILE_NAME = 'images_synthetisch_stereographic.csv'
    _STEREOGRAPHIC = True
elif hyper_parameter['label_type'][0] == 'Angular':
    _CSV_FILE_NAME = 'labels_ks_RGB.csv' #'images_synthetisch.csv'
    _STEREOGRAPHIC = False
elif hyper_parameter['label_type'][0] == 'Normalized':
    _CSV_FILE_NAME = 'images_synthetisch_normalized.csv'
    _STEREOGRAPHIC = False
else:
    assert(True, 'LabelType Invalid')

In [14]:
_USE_DATA_AUGMENTATION = False

In [15]:
_MODEL_NAME = '{}_Optimierung_Hyperparameter_v{}'.format(_DATASET_NAME, _RUN)
_IMAGE_DIR = '..\\..\\data_generation\\dataset\\{}\\'.format(_DATASET_NAME) # '..\\dataset\\{}\\'.format(_DATASET_NAME)
_CSV_FILE = _IMAGE_DIR + _CSV_FILE_NAME

_COUNTER = 0

_NET = 'RESNET' # RESNET vs VGG16

_note = '_Custom-MAE'

_NET_DIR = '{}_Regression_{}\\{}_{}_Base{}\\'.format(_RUN, _LOSS, _DATASET_NAME, hyper_parameter['label_type'][0], _note)
_LOG_DIR = '..\\{}\\{}'.format(output_path[storage], _NET_DIR)

_RESULTS_FILE = '\\..\\{}_{}_Base{}_Results.csv'.format(_DATASET_NAME, hyper_parameter['label_type'][0], _note)

if(not os.path.exists(_LOG_DIR)):
    os.makedirs(_LOG_DIR)
else:
    input('Directory >>| {} |<< existiert bereits. Fortsetzen auf eigene Gefahr! (Weiter mit Enter)'.format(_LOG_DIR))

device_file = open(_LOG_DIR + '{}'.format(_DEVICE), "a+")
device_file.close()

# Ausführung GridSearch mit Talos <a name = "Base"></a><a href = #Top>Up</a></p>

In [ ]:
import numpy as np
dummy_x = np.empty((1, 2, 3, 224, 224))
dummy_y = np.empty((1, 2))

with tf.device('/device:GPU:0'):
    
        t = ta.Scan(
            x = dummy_x,
            y = dummy_y,
            model = grid_model_base,
            params = hyper_parameter,
            experiment_name = '{}'.format(_DATASET_NAME),
            #shuffle=False,
            reduction_metric = hyper_parameter['reduction_metric'][0],
            disable_progress_bar = False,
            #print_params = True,
            clear_session = True,
            save_weights = False
        )
        

t.data.to_csv(_LOG_DIR + _RESULTS_FILE, index = True)

  0%|                                                                                          | 0/360 [00:00<?, ?it/s]

Found 16000 validated image filenames.
Found 4000 validated image filenames.
Creating bottleneck features...


161/500 [========>.....................] - ETA: 0s - loss: 21038.5918 - custom_mae: 108.55 - ETA: 1:07 - loss: 14300.2324 - custom_mae: 85.336 - ETA: 1:29 - loss: 12432.1719 - custom_mae: 83.752 - ETA: 1:41 - loss: 10827.3105 - custom_mae: 77.792 - ETA: 1:48 - loss: 10095.1553 - custom_mae: 75.533 - ETA: 1:52 - loss: 9645.9424 - custom_mae: 74.408 - ETA: 1:55 - loss: 9073.8662 - custom_mae: 71.64 - ETA: 1:57 - loss: 8636.8115 - custom_mae: 69.54 - ETA: 1:59 - loss: 8313.3506 - custom_mae: 68.20 - ETA: 2:01 - loss: 8130.7163 - custom_mae: 67.64 - ETA: 2:02 - loss: 7793.7642 - custom_mae: 66.01 - ETA: 2:03 - loss: 7734.0747 - custom_mae: 65.72 - ETA: 2:03 - loss: 7574.1182 - custom_mae: 65.26 - ETA: 2:03 - loss: 7368.5571 - custom_mae: 64.28 - ETA: 2:04 - loss: 7259.3350 - custom_mae: 63.75 - ETA: 2:05 - loss: 7036.6836 - custom_mae: 62.58 - ETA: 2:05 - loss: 7049.8364 - custom_mae: 62.78 - ETA: 2:05 - loss: 6964.3994 - custom_mae: 62.30 - ETA: 2:05 - loss: 6943.5015 - custom_mae: 62.31 

325/500 [==================>...........] - ETA: 1:33 - loss: 5702.6567 - custom_mae: 54.16 - ETA: 1:33 - loss: 5703.1089 - custom_mae: 54.15 - ETA: 1:32 - loss: 5700.1934 - custom_mae: 54.14 - ETA: 1:32 - loss: 5701.9614 - custom_mae: 54.16 - ETA: 1:32 - loss: 5698.9263 - custom_mae: 54.12 - ETA: 1:32 - loss: 5699.9224 - custom_mae: 54.11 - ETA: 1:31 - loss: 5686.9238 - custom_mae: 54.03 - ETA: 1:31 - loss: 5679.6685 - custom_mae: 53.99 - ETA: 1:31 - loss: 5678.2671 - custom_mae: 53.97 - ETA: 1:31 - loss: 5682.7290 - custom_mae: 54.00 - ETA: 1:30 - loss: 5687.6509 - custom_mae: 54.01 - ETA: 1:30 - loss: 5687.0938 - custom_mae: 54.01 - ETA: 1:30 - loss: 5685.0430 - custom_mae: 53.97 - ETA: 1:29 - loss: 5681.1060 - custom_mae: 53.94 - ETA: 1:29 - loss: 5672.3550 - custom_mae: 53.90 - ETA: 1:29 - loss: 5680.2612 - custom_mae: 53.92 - ETA: 1:29 - loss: 5686.8257 - custom_mae: 53.94 - ETA: 1:28 - loss: 5689.9639 - custom_mae: 53.95 - ETA: 1:28 - loss: 5692.1377 - custom_mae: 53.96 - ETA: 1:

490/500 [============================>.] - ETA: 48s - loss: 5488.4170 - custom_mae: 51.752 - ETA: 47s - loss: 5489.0513 - custom_mae: 51.744 - ETA: 47s - loss: 5490.5146 - custom_mae: 51.748 - ETA: 47s - loss: 5492.1309 - custom_mae: 51.759 - ETA: 47s - loss: 5489.7749 - custom_mae: 51.748 - ETA: 46s - loss: 5484.3159 - custom_mae: 51.720 - ETA: 46s - loss: 5480.4692 - custom_mae: 51.701 - ETA: 46s - loss: 5477.1274 - custom_mae: 51.680 - ETA: 45s - loss: 5483.8291 - custom_mae: 51.707 - ETA: 45s - loss: 5484.7651 - custom_mae: 51.707 - ETA: 45s - loss: 5477.7935 - custom_mae: 51.663 - ETA: 45s - loss: 5476.3013 - custom_mae: 51.644 - ETA: 44s - loss: 5473.0947 - custom_mae: 51.624 - ETA: 44s - loss: 5470.4390 - custom_mae: 51.612 - ETA: 44s - loss: 5466.6304 - custom_mae: 51.592 - ETA: 44s - loss: 5469.0264 - custom_mae: 51.597 - ETA: 43s - loss: 5463.2456 - custom_mae: 51.558 - ETA: 43s - loss: 5460.7129 - custom_mae: 51.542 - ETA: 43s - loss: 5460.7080 - custom_mae: 51.530 - ETA: 42

...

163/250 [==================>...........] - ETA: 0s - loss: 21194.1816 - custom_mae: 108.11 - ETA: 2:22 - loss: 14076.6562 - custom_mae: 85.715 - ETA: 3:10 - loss: 12576.0664 - custom_mae: 82.243 - ETA: 3:33 - loss: 12719.0801 - custom_mae: 83.387 - ETA: 3:46 - loss: 11715.2109 - custom_mae: 80.089 - ETA: 3:55 - loss: 11219.7881 - custom_mae: 78.153 - ETA: 4:01 - loss: 10603.0010 - custom_mae: 76.017 - ETA: 4:05 - loss: 10221.3955 - custom_mae: 74.928 - ETA: 4:08 - loss: 10072.8389 - custom_mae: 74.637 - ETA: 4:10 - loss: 9651.1592 - custom_mae: 73.088 - ETA: 4:11 - loss: 9496.0752 - custom_mae: 72.38 - ETA: 4:12 - loss: 9386.8506 - custom_mae: 72.04 - ETA: 4:13 - loss: 9300.1621 - custom_mae: 71.92 - ETA: 4:14 - loss: 9149.8662 - custom_mae: 71.20 - ETA: 4:14 - loss: 9001.2402 - custom_mae: 70.52 - ETA: 4:14 - loss: 8933.0840 - custom_mae: 70.42 - ETA: 4:14 - loss: 8766.6836 - custom_mae: 69.62 - ETA: 4:14 - loss: 8743.1357 - custom_mae: 69.63 - ETA: 4:14 - loss: 8707.5605 - custom_mae

250/250 [==============================] - ETA: 1:39 - loss: 6887.9443 - custom_mae: 60.70 - ETA: 1:38 - loss: 6883.3652 - custom_mae: 60.69 - ETA: 1:37 - loss: 6874.5044 - custom_mae: 60.65 - ETA: 1:36 - loss: 6878.1436 - custom_mae: 60.66 - ETA: 1:34 - loss: 6872.7646 - custom_mae: 60.62 - ETA: 1:33 - loss: 6863.9341 - custom_mae: 60.59 - ETA: 1:32 - loss: 6857.5410 - custom_mae: 60.56 - ETA: 1:31 - loss: 6853.1895 - custom_mae: 60.54 - ETA: 1:30 - loss: 6849.0103 - custom_mae: 60.50 - ETA: 1:29 - loss: 6852.8115 - custom_mae: 60.50 - ETA: 1:27 - loss: 6852.6313 - custom_mae: 60.51 - ETA: 1:26 - loss: 6852.1177 - custom_mae: 60.50 - ETA: 1:25 - loss: 6851.3452 - custom_mae: 60.50 - ETA: 1:24 - loss: 6843.3975 - custom_mae: 60.45 - ETA: 1:23 - loss: 6844.8755 - custom_mae: 60.46 - ETA: 1:22 - loss: 6840.9238 - custom_mae: 60.44 - ETA: 1:21 - loss: 6839.5723 - custom_mae: 60.42 - ETA: 1:19 - loss: 6841.2295 - custom_mae: 60.41 - ETA: 1:18 - loss: 6838.0068 - custom_mae: 60.39 - ETA: 1:

 99%|██████████████████████████████████████████████████████████████████████████▉ | 355/360 [27:05:20<25:33, 306.67s/it]

157/250 [=================>............] - ETA: 0s - loss: 21194.1816 - custom_mae: 108.11 - ETA: 2:23 - loss: 206313.4219 - custom_mae: 305.871 - ETA: 3:11 - loss: 145039.7188 - custom_mae: 240.824 - ETA: 3:34 - loss: 113437.7266 - custom_mae: 204.744 - ETA: 3:48 - loss: 94178.8906 - custom_mae: 182.176 - ETA: 3:56 - loss: 79903.6797 - custom_mae: 163.11 - ETA: 4:02 - loss: 70520.5625 - custom_mae: 151.93 - ETA: 4:06 - loss: 62559.3867 - custom_mae: 140.89 - ETA: 4:08 - loss: 56729.8086 - custom_mae: 133.58 - ETA: 4:11 - loss: 51715.2773 - custom_mae: 126.43 - ETA: 4:13 - loss: 47690.8711 - custom_mae: 121.02 - ETA: 4:13 - loss: 44556.8711 - custom_mae: 117.22 - ETA: 4:14 - loss: 41787.8711 - custom_mae: 113.62 - ETA: 4:14 - loss: 39206.8867 - custom_mae: 109.25 - ETA: 4:15 - loss: 37092.1406 - custom_mae: 106.10 - ETA: 4:15 - loss: 35340.8828 - custom_mae: 103.92 - ETA: 4:15 - loss: 33646.5703 - custom_mae: 101.47 - ETA: 4:14 - loss: 32424.4141 - custom_mae: 100.00 - ETA: 4:14 - loss

250/250 [==============================] - ETA: 1:46 - loss: 9965.1904 - custom_mae: 65.58 - ETA: 1:45 - loss: 9938.1152 - custom_mae: 65.50 - ETA: 1:44 - loss: 9916.2373 - custom_mae: 65.45 - ETA: 1:43 - loss: 9894.8203 - custom_mae: 65.41 - ETA: 1:41 - loss: 9882.6963 - custom_mae: 65.40 - ETA: 1:40 - loss: 9872.8359 - custom_mae: 65.39 - ETA: 1:39 - loss: 9859.8857 - custom_mae: 65.37 - ETA: 1:38 - loss: 9841.2520 - custom_mae: 65.35 - ETA: 1:37 - loss: 9812.5127 - custom_mae: 65.27 - ETA: 1:36 - loss: 9796.1562 - custom_mae: 65.25 - ETA: 1:34 - loss: 9775.8438 - custom_mae: 65.20 - ETA: 1:33 - loss: 9755.4980 - custom_mae: 65.15 - ETA: 1:32 - loss: 9735.3076 - custom_mae: 65.11 - ETA: 1:31 - loss: 9713.4043 - custom_mae: 65.05 - ETA: 1:30 - loss: 9693.5303 - custom_mae: 65.00 - ETA: 1:29 - loss: 9682.0322 - custom_mae: 64.97 - ETA: 1:28 - loss: 9671.5342 - custom_mae: 64.97 - ETA: 1:26 - loss: 9658.2891 - custom_mae: 64.96 - ETA: 1:25 - loss: 9638.0156 - custom_mae: 64.92 - ETA: 1:

# Copy best 10 Results to NAS if SSD Directory was selected

In [ ]:
best_results = _LOG_DIR + '..\\{}_{}_Base{}_Results.csv'.format(_DATASET_NAME, hyper_parameter['label_type'][0], _note)
df = pd.read_csv(best_results).drop(columns = ['round_epochs', 'samples', 'epochs'], axis = 0)
df = df.sort_values(hyper_parameter['monitor_value'][0], axis = 0, ascending = True, inplace = False, kind = 'quicksort', na_position = 'last')
print('Displaying: {}'.format(best_results))
df.head(10)

In [ ]:
def copy_base_directory(src, dst, data, symlinks = False, ignore = None):
    maxLen = 0
    message = ''
    
    networks_to_copy = data.head(10).index
    
    if not os.path.exists(dst):
        
        message = 'Creating Path: {}'.format(src)
        maxLen = max(maxLen, len(message))
        print(message + ' ' * (maxLen - len(message)), end = '\r')
        
        os.makedirs(dst)
        
    for item in os.listdir(src):
        
        s = os.path.join(src, item)
        d = os.path.join(dst, item)
        
        if os.path.isdir(s):
            
            message = 'Copying Directory: {}'.format(s)
            maxLen = max(maxLen, len(message))
            print(message + ' ' * (maxLen - len(message)), end = '\r')
            
            shutil.copytree(s, d, symlinks, ignore)
            
        else:
            
            if not os.path.exists(d): #or os.stat(s).st_mtime - os.stat(d).st_mtime > 1:
                for idx in networks_to_copy:
                    net = '_FC_{}.hdf5'.format(idx)
                    if net in item or '_Bottleneck_' in item or '_GPU' in item:
                        message = 'Copying File: {}'.format(s)
                        maxLen = max(maxLen, len(message))
                        print(message + ' ' * (maxLen - len(message)), end = '\r')
                
                        shutil.copy2(s, d)
        
        time.sleep(.1)    
    
    src_csv = src + _RESULTS_FILE
    dst_csv = dst + _RESULTS_FILE
    if not os.path.exists(dst_csv):
        message = 'Copying File: {}'.format(src_csv)
        maxLen = max(maxLen, len(message))
        print(message + ' ' * (maxLen - len(message)), end = '\r')
        shutil.copy2(src_csv, dst_csv)
     
    message = 'Coyping... Done'
    maxLen = max(maxLen, len(message))
    print(message + ' ' * (maxLen - len(message)), end = '\n')

    
def delete_directory(src, terminator = '\n'):
    message = ''
    maxLen = 0
    
    try:
        message = 'Deleting {}'.format(src)
        maxLen = max(maxLen, len(message))
        print(message + ' ' * (maxLen - len(message)), end = '\r')
        
        if os.path.isdir(src):
            shutil.rmtree(src)
            
        elif os.path.isfile(src):
            os.remove(src)
        
    except OSError as e:
        message = 'Error: {} : {}'.format(src, e.strerror)
        maxLen = max(maxLen, len(message))
        print(message + ' ' * (maxLen - len(message)), end = '\n')
        return
    
    message = 'Deleting... Done'
    maxLen = max(maxLen, len(message))
    print(message + ' ' * (maxLen - len(message)), end = terminator)

    
def copy_base_training(src, dst):
    copy_base_directory(src, dst, df)
    
    delete_directory(src, terminator = '\r')
    delete_directory(src + _RESULTS_FILE, terminator = '\r')
    if not os.listdir(src + '..\\'):
        delete_directory(src + '..\\', terminator = '\r')

In [ ]:
if(storage == OutputDirectory.SSD):
    _COPY_DIR = '..\\output\\{}'.format(_NET_DIR)
    copy_base_training(_LOG_DIR, _COPY_DIR)